In [1]:
import numpy as np
import xarray as xr
import pandas as pd
import matplotlib.pyplot as plt
import os
import multiprocessing as mp
from tqdm import tqdm
from scipy.signal import detrend
from scipy.stats import linregress
#import rioxarray as rxr
import torch
from copy import copy
import matplotlib
import cartopy 
import cartopy.crs as ccrs
import warnings
import calendar
from datetime import date, timedelta

In [2]:
from matplotlib import rcParams
from matplotlib.ticker import MaxNLocator
import matplotlib.dates as mdates

rcParams['font.family'] = 'Inter'
rcParams['font.size'] = 12
rcParams['figure.figsize'] = [5.0, 5.0]
rcParams['figure.dpi'] = 300
rcParams['xtick.direction'] = 'in'
rcParams['ytick.direction'] = 'in'

## Plot Annual SIF Trend and Compare with GOSIF, CSIF

In [3]:
def get_file_list(product_dir):
    filelist=[]
    for file in sorted(os.listdir(product_dir)):
        filelist.append(os.path.join(product_dir, file))
    return filelist

BASE_DIR = "AVHRR/"

LCSIF_v30_DIR=os.path.join(BASE_DIR, "data/LCSIF_v3")
MODIS_LCSIF_DIR=os.path.join(BASE_DIR, "data/MODIS_LCSIF_v3")
MODIS_LCREF_DIR=os.path.join(BASE_DIR, "data/MODIS_LCREF_v3")
LCSIF_v31_DIR=os.path.join(BASE_DIR, "data/LCSIF_v3.1/")
LCREF_v31_DIR=os.path.join(BASE_DIR, "data/LCREF_v3.1/")
LTDR_LCSIF = os.path.join(BASE_DIR, "data/LTDR_LCSIF/")

LCSIF_v31_LIST=[f for f in get_file_list(LCSIF_v31_DIR) if "SNOW" in f]
LCREF_v31_LIST=[f for f in get_file_list(LCREF_v31_DIR) if "SNOW" in f]
LTDR_LCSIF_LIST =get_file_list(LTDR_LCSIF)

MODIS_LCSIF_FILE_LIST=[f for f in get_file_list(MODIS_LCSIF_DIR) if "SNOW" in f]
MODIS_LCREF_FILE_LIST=[f for f in get_file_list(MODIS_LCREF_DIR) if "SNOW" in f]

LCSIF_v31_PRE_2001_PERIOD_FILE_LIST=LCSIF_v31_LIST[0:19*24]
LCSIF_v31_POST_2001_PERIOD_FILE_LIST=LCSIF_v31_LIST[19*24:]

LCREF_v31_PRE_2001_PERIOD_FILE_LIST=LCREF_v31_LIST[0:19*24]
LCREF_v31_POST_2001_PERIOD_FILE_LIST=LCREF_v31_LIST[19*24:]

LTDR_LCSIF_PRE_2001_PERIOD_FILE_LIST=LTDR_LCSIF_LIST[0:19*24]
LTDR_LCSIF_POST_2001_PERIOD_FILE_LIST=LTDR_LCSIF_LIST[19*24:]

CSIF_DIR="AVHRR/data/CSIF_v2/"
fig_dir="./figs/"
DATA_DIR=os.path.join(BASE_DIR, "data/")

In [4]:
growing_season_flag = np.invert(np.load(os.path.join(DATA_DIR, "growing_season_monthly_flag_5C.npy")))
area_weight=xr.open_dataset(os.path.join(DATA_DIR, "CMG_0.05Degree_Area_WGS84.nc")).area.values

NAN_MASK = xr.open_dataset(os.path.join(DATA_DIR, "processed/LCSIF_LCREF_MASK.nc")).LCSIF_LCREF_MASK.values

In [5]:
def compute_annual_mean_from_biweekly(file_list, var_name="sif_clear_daily"):
    annual_mean_list=[]
    with warnings.catch_warnings():
        warnings.filterwarnings('ignore', r'All-NaN (slice|axis) encountered')
        warnings.filterwarnings('ignore', r'Mean of empty (slice|axis)')
        for YEAR in tqdm(np.array(file_list).reshape(-1,24)):
            year_list=[]
            for i in range(12):
                first_half_month = xr.open_dataset(YEAR[i*2])[var_name].values[0]
                first_half_month[NAN_MASK]=np.nan
                second_half_month = xr.open_dataset(YEAR[i*2 + 1])[var_name].values[0]  
                second_half_month[NAN_MASK]=np.nan
                mvc = np.nanmax(np.stack([first_half_month, second_half_month]), axis=0)
                mvc[growing_season_flag[i, :, :]] = np.nan
                monthly_mean = np.nansum(mvc * area_weight) / np.nansum(area_weight[np.invert(np.isnan(mvc * area_weight))])
                year_list.append(monthly_mean)
            annual_mean_list.append(np.nanmean(year_list))
        return np.array(annual_mean_list)

In [9]:
sif_v31_pre_2001_weighted_spatial_annual_mean_list=compute_annual_mean_from_biweekly(LCSIF_v31_PRE_2001_PERIOD_FILE_LIST)
    
sif_v31_post_2001_weighted_spatial_annual_mean_list=compute_annual_mean_from_biweekly(LCSIF_v31_POST_2001_PERIOD_FILE_LIST)


100%|███████████████████████████████████████████| 22/22 [04:14<00:00, 11.55s/it]


In [10]:
sif_v31_pre_2001_weighted_spatial_annual_mean_list.shape

(19,)

In [11]:
sif_v31_pre_2001_weighted_spatial_annual_mean_list_all=compute_annual_mean_from_biweekly(LCSIF_v31_PRE_2001_PERIOD_FILE_LIST,
                                                                                         var_name="sif_all_daily")
    
sif_v31_post_2001_weighted_spatial_annual_mean_list_all=compute_annual_mean_from_biweekly(LCSIF_v31_POST_2001_PERIOD_FILE_LIST,
                                                                                          var_name="sif_all_daily")


100%|███████████████████████████████████████████| 22/22 [03:58<00:00, 10.86s/it]


In [12]:
ltdr_lcsif_pre_2001_weighted_spatial_annual_mean_list=compute_annual_mean_from_biweekly(LTDR_LCSIF_PRE_2001_PERIOD_FILE_LIST)
    
ltdr_lcsif_post_2001_weighted_spatial_annual_mean_list=compute_annual_mean_from_biweekly(LTDR_LCSIF_POST_2001_PERIOD_FILE_LIST)


100%|███████████████████████████████████████████| 22/22 [04:26<00:00, 12.11s/it]


In [13]:
modis_sif_weighted_spatial_annual_mean_list=compute_annual_mean_from_biweekly(MODIS_LCSIF_FILE_LIST)
    
modis_sif_weighted_spatial_annual_mean_list_all=compute_annual_mean_from_biweekly(MODIS_LCSIF_FILE_LIST, var_name="sif_all_daily")


100%|███████████████████████████████████████████| 22/22 [03:52<00:00, 10.59s/it]


In [25]:
def print_reg_string(x, y):
    reg=linregress(x, y)
    if reg.intercept < 0:
        return "{:.5f}".format(reg.slope) + "x{:.5f}".format(reg.intercept)
    else:
        return "{:.5f}".format(reg.slope) + "x+{:.5f}".format(reg.intercept)

fig, ax = plt.subplots(1,1, figsize=(10,5), dpi=300)

line1, = ax.plot(np.arange(2001,2023), modis_sif_weighted_spatial_annual_mean_list, 
         linestyle='--', marker='o', color="purple", label="LCSIF-MODIS:")

line2, = ax.plot(np.arange(1982,2023), np.concatenate([np.array(sif_v31_pre_2001_weighted_spatial_annual_mean_list),
                                               np.array(sif_v31_post_2001_weighted_spatial_annual_mean_list)]),
         linestyle='--', marker='o', color="#1F449C", label="LCSIF-AVHRR:")


line3 ,= ax.plot(np.arange(1982,2023), np.concatenate([np.array(ltdr_lcsif_pre_2001_weighted_spatial_annual_mean_list),
                                               np.array(ltdr_lcsif_post_2001_weighted_spatial_annual_mean_list)]), color="grey", linestyle='--', label="SIF-LTDR:")


# Create a legend for the first line.
first_legend = ax.legend(handles=[line1, line2], loc='upper left', frameon=False, labelspacing = 1.8)

# Add the legend manually to the Axes.
ax.add_artist(first_legend)

# Create another legend for the second line.
ax.legend(handles=[line3],  frameon=False,
          bbox_to_anchor=(2001, 0.1125), bbox_transform=ax.transData)



ax.plot([2000.5, 2000.5], [0,1], "k--", linewidth=0.8, alpha=0.3)
#plt.legend(loc="upper left", frameon=False, labelspacing = 1.8)
plt.ylim(0.10, 0.185)

plt.text(1989, 0.18, print_reg_string(np.arange(2001,2023), modis_sif_weighted_spatial_annual_mean_list) + " (2001-2022)", fontsize=11)

plt.text(1989, 0.1725, print_reg_string(np.arange(1982,2001),
                                       np.array(sif_v31_pre_2001_weighted_spatial_annual_mean_list)) + " (1982-2000)", fontsize=11)
plt.text(1989, 0.1695, print_reg_string(np.arange(2001,2023),
                                       np.array(sif_v31_post_2001_weighted_spatial_annual_mean_list)) + " (2001-2022)", fontsize=11)
plt.text(2008.5, 0.1085, print_reg_string(np.arange(1982,2001),
                                       np.array(ltdr_lcsif_pre_2001_weighted_spatial_annual_mean_list)) + " (1982-2000)", fontsize=11)
plt.text(2008.5, 0.1055, print_reg_string(np.arange(2001,2023),
                                       np.array(ltdr_lcsif_post_2001_weighted_spatial_annual_mean_list)) + " (2001-2022)", fontsize=11)



plt.text(1988, 0.135, "AVHRR Period")
plt.text(1985, 0.132, "(calibrated against MODIS)")

plt.text(2008, 0.135, "MODIS Period")

plt.ylabel("Annual Mean SIF \n (mW m$^{-2}$ nm$^{-1}$ sr$^{-1}$)")
plt.tick_params(top=True, bottom=True, left=True, right=True)
#plt.savefig(fig_dir + "LCSIF_timeseries_v31.png", dpi=300)


## Spatial Trend and Correlation Analysis

In [6]:
def downsample_sif(sif, weight, count_threshold = 0.5):
    with torch.no_grad():
        conv = torch.nn.Conv2d(1, 1, (10,10), 10, bias=False)
        conv.weight = torch.nn.Parameter(torch.ones_like(conv.weight))
        sif_tensor = torch.tensor(sif).expand(1, 3600, 7200).float()
        weight_tensor = torch.tensor(weight).expand(1, 3600, 7200).float()
        weighted_sif_tensor = sif_tensor * weight_tensor
        weighted_count_tensor = np.invert(torch.isnan(sif_tensor)).type(torch.float) * weight_tensor
        weighted_sif_tensor[torch.isnan(sif_tensor)] = 0.0
        
        downsampled = conv(weighted_sif_tensor).numpy()[0]
        downsampled_weight = conv(weight_tensor).numpy()[0]
        downsampled_weighted_count= conv(weighted_count_tensor).numpy()[0]

    downsampled = downsampled / downsampled_weighted_count
    downsampled[downsampled_weighted_count < downsampled_weight * count_threshold] = np.nan
    return downsampled

In [7]:
def lag_linregress_3D(x, y, lagx=0, lagy=0):
    """
        Input: Two xr.Datarrays of any dimensions with the first dim being time. 
        Thus the input data could be a 1D time series, or for example, have three dimensions (time,lat,lon). 
        Datasets can be provied in any order, but note that the regression slope and intercept will be calculated
        for y with respect to x.
        Output: Covariance, correlation, regression slope and intercept, p-value, and standard error on regression
        between the two datasets along their aligned time dimension.  
        Lag values can be assigned to either of the data, with lagx shifting x, and lagy shifting y, with the specified lag amount.
        Reference: https://hrishichandanpurkar.blogspot.com/2017/09/vectorized-functions-for-correlation.html
    """ 
    
    with warnings.catch_warnings():
        warnings.filterwarnings('ignore', r'Degrees of freedom <= 0 for slice')
        warnings.filterwarnings('ignore', r'invalid value encountered in sqrt')
    
        #1. Ensure that the data are properly alinged to each other. 
        x,y = xr.align(x,y)


        #2. Add lag information if any, and shift the data accordingly
        if lagx!=0:
            #If x lags y by 1, x must be shifted 1 step backwards. 
            #But as the 'zero-th' value is nonexistant, xr assigns it as invalid (nan). Hence it needs to be dropped
            x   = x.shift(time = -lagx).dropna(dim='time')
            #Next important step is to re-align the two datasets so that y adjusts to the changed coordinates of x
            x,y = xr.align(x,y)

        if lagy!=0:
            y   = y.shift(time = -lagy).dropna(dim='time')
            x,y = xr.align(x,y)

        #3. Compute data length, mean and standard deviation along time axis for further use: 
        #n     = x.shape[0]
        n = np.sum(np.invert(np.isnan(x.values)) & np.invert(np.isnan(y.values)), axis=0)
        xmean = x.mean(axis=0)
        ymean = y.mean(axis=0)
        xstd  = x.std(axis=0)
        ystd  = y.std(axis=0)

        #4. Compute covariance along time axis
        cov   =  np.sum((x - xmean)*(y - ymean), axis=0)/(n)

        #5. Compute correlation along time axis
        cor   = cov/(xstd*ystd)

        #6. Compute regression slope and intercept:
        slope     = cov/(xstd**2)
        intercept = ymean - xmean*slope  

        #7. Compute P-value and standard error
        #Compute t-statistics
        tstats = cor*np.sqrt(n-2)/np.sqrt(1-cor**2)
        stderr = slope/tstats

        from scipy.stats import t
        pval   = t.sf(tstats, n-2)*2
        pval   = xr.DataArray(pval, dims=cor.dims, coords=cor.coords)

        return cov,cor,slope,intercept,pval,stderr

In [64]:
sif_v31_pre_2001_annual_list=[]
with warnings.catch_warnings():
    warnings.filterwarnings('ignore', r'All-NaN (slice|axis) encountered')
    warnings.filterwarnings('ignore', r'Mean of empty (slice|axis)')
    warnings.filterwarnings('ignore', r'invalid value encountered in divide')
    for YEAR in tqdm(np.array(LCSIF_v31_PRE_2001_PERIOD_FILE_LIST).reshape(-1,24)):
        year_list=[]
        for i in range(12):
            first_half_month = xr.open_dataset(YEAR[i*2]).sif_clear_daily.values[0]
            first_half_month[NAN_MASK]=np.nan
            second_half_month = xr.open_dataset(YEAR[i*2 + 1]).sif_clear_daily.values[0]
            second_half_month[NAN_MASK]=np.nan
            monthly_mvc = np.nanmax(np.stack([first_half_month, second_half_month]), axis=0)
            monthly_mvc[growing_season_flag[i, :, :]] = np.nan
            year_list.append(monthly_mvc)
        year_stack = np.stack(year_list)
        year_mean = np.nanmean(year_stack, axis=0)
        sif_v31_pre_2001_annual_list.append(downsample_sif(year_mean, area_weight))
        
sif_v31_post_2001_annual_list=[]
with warnings.catch_warnings():
    warnings.filterwarnings('ignore', r'All-NaN (slice|axis) encountered')
    warnings.filterwarnings('ignore', r'Mean of empty (slice|axis)')
    warnings.filterwarnings('ignore', r'invalid value encountered in divide')
    for YEAR in tqdm(np.array(LCSIF_v31_POST_2001_PERIOD_FILE_LIST).reshape(-1,24)):
        year_list=[]
        for i in range(12):
            first_half_month = xr.open_dataset(YEAR[i*2]).sif_clear_daily.values[0]
            first_half_month[NAN_MASK]=np.nan
            second_half_month = xr.open_dataset(YEAR[i*2 + 1]).sif_clear_daily.values[0]
            second_half_month[NAN_MASK]=np.nan
            monthly_mvc = np.nanmax(np.stack([first_half_month, second_half_month]), axis=0)
            monthly_mvc[growing_season_flag[i, :, :]] = np.nan
            year_list.append(monthly_mvc)
        year_stack = np.stack(year_list)
        year_mean = np.nanmean(year_stack, axis=0)
        sif_v31_post_2001_annual_list.append(downsample_sif(year_mean, area_weight))
        
modis_sif_annual_list=[]
with warnings.catch_warnings():
    warnings.filterwarnings('ignore', r'All-NaN (slice|axis) encountered')
    warnings.filterwarnings('ignore', r'Mean of empty (slice|axis)')
    warnings.filterwarnings('ignore', r'invalid value encountered in divide')
    for YEAR in tqdm(np.array(MODIS_LCSIF_FILE_LIST).reshape(-1,24)):
        year_list=[]
        for i in range(12):
            first_half_month = xr.open_dataset(YEAR[i*2]).sif_clear_daily.values[0]
            first_half_month[NAN_MASK]=np.nan
            second_half_month = xr.open_dataset(YEAR[i*2 + 1]).sif_clear_daily.values[0]
            second_half_month[NAN_MASK]=np.nan
            monthly_mvc = np.nanmax(np.stack([first_half_month, second_half_month]), axis=0)
            monthly_mvc[growing_season_flag[i, :, :]] = np.nan
            year_list.append(monthly_mvc)
        year_stack = np.stack(year_list)
        year_mean = np.nanmean(year_stack, axis=0)
        modis_sif_annual_list.append(downsample_sif(year_mean, area_weight))
        
        
sif_v31_pre_2001_annual_list_all=[]
with warnings.catch_warnings():
    warnings.filterwarnings('ignore', r'All-NaN (slice|axis) encountered')
    warnings.filterwarnings('ignore', r'Mean of empty (slice|axis)')
    warnings.filterwarnings('ignore', r'invalid value encountered in divide')
    for YEAR in tqdm(np.array(LCSIF_v31_PRE_2001_PERIOD_FILE_LIST).reshape(-1,24)):
        year_list=[]
        for i in range(12):
            first_half_month = xr.open_dataset(YEAR[i*2]).sif_all_daily.values[0]
            first_half_month[NAN_MASK]=np.nan
            second_half_month = xr.open_dataset(YEAR[i*2 + 1]).sif_all_daily.values[0]
            second_half_month[NAN_MASK]=np.nan
            monthly_mvc = np.nanmax(np.stack([first_half_month, second_half_month]), axis=0)
            monthly_mvc[growing_season_flag[i, :, :]] = np.nan
            year_list.append(monthly_mvc)
        year_stack = np.stack(year_list)
        year_mean = np.nanmean(year_stack, axis=0)
        sif_v31_pre_2001_annual_list_all.append(downsample_sif(year_mean, area_weight))
        
        
sif_v31_post_2001_annual_list_all=[]
with warnings.catch_warnings():
    warnings.filterwarnings('ignore', r'All-NaN (slice|axis) encountered')
    warnings.filterwarnings('ignore', r'Mean of empty (slice|axis)')
    warnings.filterwarnings('ignore', r'invalid value encountered in divide')
    for YEAR in tqdm(np.array(LCSIF_v31_POST_2001_PERIOD_FILE_LIST).reshape(-1,24)):
        year_list=[]
        for i in range(12):
            first_half_month = xr.open_dataset(YEAR[i*2]).sif_all_daily.values[0]
            first_half_month[NAN_MASK]=np.nan
            second_half_month = xr.open_dataset(YEAR[i*2 + 1]).sif_all_daily.values[0]
            second_half_month[NAN_MASK]=np.nan
            monthly_mvc = np.nanmax(np.stack([first_half_month, second_half_month]), axis=0)
            monthly_mvc[growing_season_flag[i, :, :]] = np.nan
            year_list.append(monthly_mvc)
        year_stack = np.stack(year_list)
        year_mean = np.nanmean(year_stack, axis=0)
        sif_v31_post_2001_annual_list_all.append(downsample_sif(year_mean, area_weight))

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 22/22 [03:40<00:00, 10.01s/it]


In [65]:
LOW_SIF_MASK = np.nanmean(np.array(sif_v31_pre_2001_annual_list + sif_v31_post_2001_annual_list), axis=0) < 0.03
np.save(os.path.join(BASE_DIR, "data/processed/low_sif_mask_0.03.npy",LOW_SIF_MASK))

In [8]:
sif_v31_pre_2001_annual_tensor = np.load(os.path.join(BASE_DIR, "data/snow_sif_v31_pre_2001_annual_tensor.npy"))
sif_v31_post_2001_annual_tensor = np.load(os.path.join(BASE_DIR, "data/snow_sif_v31_post_2001_annual_tensor.npy"))
modis_sif_annual_tensor = np.load(os.path.join(BASE_DIR, "data/snow_modis_sif_annual_tensor.npy"))
lcsif_annual_tensor_all = np.load(os.path.join(BASE_DIR, "data/snow_sif_v31_annual_all_tensor.npy"))

In [9]:
LOW_SIF_MASK = np.load(os.path.join(BASE_DIR, "data/processed/low_sif_mask_0.03.npy"))
#for i in range(len(sif_v31_pre_2001_annual_list)):
#    sif_v31_pre_2001_annual_list[i][LOW_SIF_MASK] = np.nan
    
#sif_v31_pre_2001_annual_tensor = np.stack(sif_v31_pre_2001_annual_list)

sif_v31_pre_2001_annual_da = xr.DataArray(sif_v31_pre_2001_annual_tensor, dims=["time", "lat", "lon"], coords={"time":np.arange(1982,2001),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})
sif_v31_pre_2001_annual_time_da = xr.DataArray(np.stack([np.full((360,720), i).astype(np.float32) for i in sif_v31_pre_2001_annual_da.time]), dims=["time", "lat", "lon"], coords={"time":np.arange(1982,2001),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})

sif_v31_pre_2001_cov,sif_v31_pre_2001_cor,sif_v31_pre_2001_slope,sif_v31_pre_2001_intercept,sif_v31_pre_2001_pval,sif_v31_pre_2001_stderr = lag_linregress_3D(sif_v31_pre_2001_annual_time_da, sif_v31_pre_2001_annual_da)
sif_v31_pre_2001_slope_copy = copy(sif_v31_pre_2001_slope.values)
sif_v31_pre_2001_slope_copy[np.isnan(sif_v31_pre_2001_annual_tensor[0])] = np.nan

In [10]:
sif_v31_post_2001_annual_da = xr.DataArray(sif_v31_post_2001_annual_tensor, dims=["time", "lat", "lon"], coords={"time":np.arange(2001,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})
sif_v31_post_2001_annual_time_da = xr.DataArray(np.stack([np.full((360,720), i).astype(np.float32) for i in sif_v31_post_2001_annual_da.time]), dims=["time", "lat", "lon"], coords={"time":np.arange(2001,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})

sif_v31_post_2001_cov,sif_v31_post_2001_cor,sif_v31_post_2001_slope,sif_v31_post_2001_intercept,sif_v31_post_2001_pval,sif_v31_post_2001_stderr = lag_linregress_3D(sif_v31_post_2001_annual_time_da, sif_v31_post_2001_annual_da)
sif_v31_post_2001_slope_copy = copy(sif_v31_post_2001_slope.values)
sif_v31_post_2001_slope_copy[np.isnan(sif_v31_post_2001_annual_tensor[0])] = np.nan

In [11]:
lcsif_annual_tensor = np.vstack([sif_v31_pre_2001_annual_da, sif_v31_post_2001_annual_da])

lcsif_annual_da = xr.DataArray(lcsif_annual_tensor, dims=["time", "lat", "lon"], coords={"time":np.arange(1982,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})
lcsif_annual_time_da = xr.DataArray(np.stack([np.full((360,720), i).astype(np.float32) for i in lcsif_annual_da.time]), dims=["time", "lat", "lon"], coords={"time":np.arange(1982,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})

lcsif_cov,lcsif_cor,lcsif_slope,lcsif_intercept,lcsif_pval,lcsif_stderr = lag_linregress_3D(lcsif_annual_time_da, lcsif_annual_da)

lcsif_slope_copy = copy(lcsif_slope.values)
lcsif_slope_copy[np.isnan(lcsif_annual_tensor[0])] = np.nan

In [12]:
#lcsif_annual_tensor_all = np.stack(sif_v31_pre_2001_annual_list_all + sif_v31_post_2001_annual_list_all)

lcsif_annual_da_all = xr.DataArray(lcsif_annual_tensor_all, dims=["time", "lat", "lon"], coords={"time":np.arange(1982,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})

clear_all_cov,clear_all_cor,clear_all_slope,clear_all_intercept,clear_all_pval,clear_all_stderr = lag_linregress_3D(lcsif_annual_da_all, lcsif_annual_da)

clear_all_cor_copy = copy(clear_all_cor.values)
clear_all_cor_copy[np.isnan(lcsif_annual_tensor_all[0])] = np.nan

In [13]:
#for i in range(len(modis_sif_annual_list)):
#    modis_sif_annual_list[i][LOW_SIF_MASK] = np.nan
    
#modis_sif_annual_tensor = np.stack(modis_sif_annual_list)

modis_sif_annual_da = xr.DataArray(modis_sif_annual_tensor, dims=["time", "lat", "lon"], coords={"time":np.arange(2001,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})
modis_sif_annual_time_da = xr.DataArray(np.stack([np.full((360,720), i).astype(np.float32) for i in modis_sif_annual_da.time]), dims=["time", "lat", "lon"], coords={"time":np.arange(2001,2023),
                                            "lat":np.flip(np.arange(-89.75,90, 0.5)),
                                            "lon":np.arange(-179.75, 180, 0.5)})

modis_sif_cov,modis_sif_cor,modis_sif_slope,modis_sif_intercept,modis_sif_pval,modis_sif_stderr = lag_linregress_3D(modis_sif_annual_time_da, modis_sif_annual_da)

modis_sif_slope_copy = copy(modis_sif_slope.values)
modis_sif_slope_copy[np.isnan(modis_sif_annual_tensor[0])] = np.nan

In [14]:
avhrr_modis_cov,avhrr_modis_cor,avhrr_modis_slope,avhrr_modis_intercept,avhrr_modis_pval,avhrr_modis_stderr = lag_linregress_3D(sif_v31_post_2001_annual_da, modis_sif_annual_da)
avhrr_modis_cor_copy = copy(avhrr_modis_cor.values)
avhrr_modis_cor_copy[np.isnan(modis_sif_annual_tensor[0])] = np.nan
avhrr_modis_cor_copy[np.isnan(sif_v31_post_2001_annual_tensor[0])] = np.nan

In [15]:
def plot_pattern(fig, ax1, ax2, data_mat, p_val, text_str, cor=False, bound_norm_list=None, bound_norm_tick=None, bound_norm_tick_label=None, lat_xlim=None, lat_norm_tick=None, lat_norm_tick_label=None):
    count_too_small = 720 - np.sum(np.isnan(data_mat), axis=1) < 25
    
    if not cor or bound_norm_list is not None:
        data_mat_mean = np.nanmean(10 * data_mat, axis=1)
        lower_ribbon = (data_mat_mean-np.nanstd(10 * data_mat, axis=1))
        upper_ribbon = (data_mat_mean+np.nanstd(10 * data_mat, axis=1))
    else:
        data_mat_mean = np.nanmean(data_mat, axis=1)
        lower_ribbon = (data_mat_mean-np.nanstd(data_mat, axis=1))
        upper_ribbon = (data_mat_mean+np.nanstd(data_mat, axis=1))
        
        data_mat_mean[count_too_small] = np.nan
        lower_ribbon[count_too_small] = np.nan
        upper_ribbon[count_too_small] = np.nan
        

    ax1.fill_betweenx(np.flip(np.arange(-89.75,90, 0.5)),
                      lower_ribbon, upper_ribbon, color="lightgray")
    ax1.plot(data_mat_mean, np.flip(np.arange(-89.75,90, 0.5)), color="darkmagenta")
    
    if not cor:
        if lat_xlim is not None:
            ax1.set_xlim(lat_xlim[0], lat_xlim[1])
            ax1.set_xticks(lat_norm_tick, lat_norm_tick_label)
        else:
            ax1.set_xlim(-0.015, 0.015)
            ax1.set_xticks([-0.01, 0, 0.01], ['-0.01', '0', '0.01'])
        ax1.set_yticks([90, 60, 30, 0, -30, -60, -90], ['90$^{\circ}N$', '60$^{\circ}N$', '30$^{\circ}N$', '0$^{\circ}$', '30$^{\circ}S$', '60$^{\circ}S$', '90$^{\circ}S$'])
        ax1.set_ylim(-90, 90)

    else:
        ax1.set_xlim(0,1)
        ax1.set_xticks([0.2, 0.6, 1], ['0.2', '0.6', '1'])
        ax1.set_yticks([90, 60, 30, 0, -30, -60, -90], ['90$^{\circ}N$', '60$^{\circ}N$', '30$^{\circ}N$', '0$^{\circ}$', '30$^{\circ}S$', '60$^{\circ}S$', '90$^{\circ}S$'])
        ax1.set_ylim(-90, 90)
        

    if not cor:
        cmap = matplotlib.colors.LinearSegmentedColormap.from_list("", ["darkmagenta","white", "darkgreen"])
        if bound_norm_list is not None:
            norm=matplotlib.colors.BoundaryNorm(bound_norm_list, matplotlib.cm.hot.N, extend='both')
            im2=ax2.imshow(data_mat, transform=ccrs.PlateCarree(), aspect='auto', extent=[-180,180,-90,90],interpolation="none", norm=norm, cmap=cmap)
            cbar = fig.colorbar(im2, ax=ax2, orientation="vertical", fraction=0.027, ticks=bound_norm_tick)
            cbar.ax.set_yticklabels(bound_norm_tick_label)
        else:
            norm=matplotlib.colors.BoundaryNorm([-0.03, -0.025, -0.02, -0.015, -0.01, -0.005, 0, 0.005, 0.01, 0.015, 0.02, 0.025, 0.03], matplotlib.cm.hot.N, extend='both')
            im2=ax2.imshow(data_mat * 10, transform=ccrs.PlateCarree(), aspect='auto', extent=[-180,180,-90,90],interpolation="none", norm=norm, cmap=cmap)
            cbar = fig.colorbar(im2, ax=ax2, orientation="vertical", fraction=0.027, ticks=[-0.03,-0.02, -0.01, 0, 0.01, 0.02, 0.03])
            cbar.ax.set_yticklabels(['-0.03', '-0.02', '-0.01', '0', '0.01', '0.02', '0.03'])
        
    else:
        cmap = matplotlib.colors.LinearSegmentedColormap.from_list("", ["cornsilk","yellow", "darkred"])
        norm=matplotlib.colors.BoundaryNorm([0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1], matplotlib.cm.hot.N)
        im2=ax2.imshow(data_mat, transform=ccrs.PlateCarree(), aspect='auto', extent=[-180,180,-90,90],interpolation="none", cmap=cmap, norm=norm)
        cbar = fig.colorbar(im2, ax=ax2, orientation="vertical", fraction=0.027, ticks=[0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1])
        cbar.ax.set_yticklabels(['0','0.1', '0.2', '0.3', '0.4', '0.5', '0.6', '0.7', '0.8', '0.9', '1'])
        
    ax2.add_feature(cartopy.feature.OCEAN, zorder=0, color="white")
    ax2.coastlines()
    gl=ax2.gridlines(crs=ccrs.PlateCarree(), draw_labels=True,
                      linewidth=1, color='gray', alpha=0.5, linestyle='--')
    gl.right_labels=False
    gl.top_labels=False
    gl.left_labels=False

    if not (p_val is None):
        ax2.contourf(np.arange(-179.75, 180, 0.5), np.flip(np.arange(-89.75,90, 0.5)), p_val < 0.05, levels=1,
                          colors="white", hatches=['', '...'] , extend='neither', alpha=0)
    ax2.text(-180, 95, text_str, fontsize=25)

In [24]:
from matplotlib import gridspec
f = plt.figure(figsize=(25,22), dpi=300)
gs1 = gridspec.GridSpec(3, 2, width_ratios=[0.2, 2.2],
                       height_ratios=[1, 1, 1], wspace=0.02)
gs1.update(left=0.05, right=0.48, wspace=0.05)

ax1 = plt.subplot(gs1[0, 0])
ax2 = plt.subplot(gs1[0, 1], projection=ccrs.PlateCarree())
ax3 = plt.subplot(gs1[1, 0])
ax4 = plt.subplot(gs1[1, 1], projection=ccrs.PlateCarree())
ax5 = plt.subplot(gs1[2, 0])
ax6 = plt.subplot(gs1[2, 1], projection=ccrs.PlateCarree())

gs2 = gridspec.GridSpec(3, 2, width_ratios=[0.2, 2.2],
                       height_ratios=[1, 1, 1], wspace=0.02)
gs2.update(left=0.55, right=0.98, wspace=0.05)


ax7 = plt.subplot(gs2[0, 0])
ax8 = plt.subplot(gs2[0, 1], projection=ccrs.PlateCarree())
ax9 = plt.subplot(gs2[1, 0])
ax10 = plt.subplot(gs2[1, 1], projection=ccrs.PlateCarree())
ax11 = plt.subplot(gs2[2, 0])
ax12 = plt.subplot(gs2[2, 1], projection=ccrs.PlateCarree())

plot_pattern(f, ax1, ax2, lcsif_slope_copy, lcsif_pval.values, "(a) LCSIF-AVHRR Trend (1982-2022)")
plot_pattern(f, ax3, ax4, sif_v31_pre_2001_slope_copy, sif_v31_pre_2001_pval.values, "(b) LCSIF-AVHRR Trend (1982-2000)")
plot_pattern(f, ax5, ax6, sif_v31_post_2001_slope_copy, sif_v31_post_2001_pval.values, "(c) LCSIF-AVHRR Trend (2001-2022)")
plot_pattern(f, ax7, ax8, clear_all_cor_copy, clear_all_pval.values, "(d) r(clear-sky, all-sky)", True)
plot_pattern(f, ax9, ax10, avhrr_modis_cor_copy, avhrr_modis_pval.values, "(e) r(LCSIF-AVHRR, LCSIF-MODIS)", True)
plot_pattern(f, ax11, ax12, modis_sif_slope_copy, modis_sif_pval.values, "(f) LCSIF-MODIS Trend (2001-2022) ")

plt.savefig("snow_sif_trend_spatial_nan_max_3.1.png", dpi=300)
